![Piggy bank](piggy_bank.jpg)

Personal loans are a lucrative revenue stream for banks. The typical interest rate of a two-year loan in the United Kingdom is [around 10%](https://www.experian.com/blogs/ask-experian/whats-a-good-interest-rate-for-a-personal-loan/). This might not sound like a lot, but in September 2022 alone UK consumers borrowed [around £1.5 billion](https://www.ukfinance.org.uk/system/files/2022-12/Household%20Finance%20Review%202022%20Q3-%20Final.pdf), which would mean approximately £300 million in interest generated by banks over two years!

You have been asked to work with a bank to clean the data they collected as part of a recent marketing campaign, which aimed to get customers to take out a personal loan. They plan to conduct more marketing campaigns going forward so would like you to ensure it conforms to the specific structure and data types that they specify so that they can then use the cleaned data you provide to set up a PostgreSQL database, which will store this campaign's data and allow data from future campaigns to be easily imported.

They have supplied you with a csv file called `"bank_marketing.csv"`, which you will need to clean, reformat, and split the data, saving three final csv files. Specifically, the three files should have the names and contents as outlined below:

## `client.csv`

| column           | data type | description                                                | cleaning requirements                                             |
| ---------------- | --------- | ---------------------------------------------------------- | ----------------------------------------------------------------- |
| `client_id`      | `integer` | Client ID                                                  | N/A                                                               |
| `age`            | `integer` | Client's age in years                                      | N/A                                                               |
| `job`            | `object`  | Client's type of job                                       | Change `"."` to `"_"`                                             |
| `marital`        | `object`  | Client's marital status                                    | N/A                                                               |
| `education`      | `object`  | Client's level of education                                | Change `"."` to `"_"` and `"unknown"` to `np.NaN`                 |
| `credit_default` | `bool`    | Whether the client's credit is in default                  | Convert to `boolean` data type:<br> `1` if `"yes"`, otherwise `0` |
| `mortgage`       | `bool`    | Whether the client has an existing mortgage (housing loan) | Convert to boolean data type:<br> `1` if `"yes"`, otherwise `0`   |

<br>

## `campaign.csv`

| column                       | data type  | description                                                       | cleaning requirements                                                                                                                                  |
| ---------------------------- | ---------- | ----------------------------------------------------------------- | ------------------------------------------------------------------------------------------------------------------------------------------------------ |
| `client_id`                  | `integer`  | Client ID                                                         | N/A                                                                                                                                                    |
| `number_contacts`            | `integer`  | Number of contact attempts to the client in the current campaign  | N/A                                                                                                                                                    |
| `contact_duration`           | `integer`  | Last contact duration in seconds                                  | N/A                                                                                                                                                    |
| `previous_campaign_contacts` | `integer`  | Number of contact attempts to the client in the previous campaign | N/A                                                                                                                                                    |
| `previous_outcome`           | `bool`     | Outcome of the previous campaign                                  | Convert to boolean data type:<br> `1` if `"success"`, otherwise `0`.                                                                                   |
| `campaign_outcome`           | `bool`     | Outcome of the current campaign                                   | Convert to boolean data type:<br> `1` if `"yes"`, otherwise `0`.                                                                                       |
| `last_contact_date`          | `datetime` | Last date the client was contacted                                | Create from a combination of `day`, `month`, and a newly created `year` column (which should have a value of `2022`); <br> **Format =** `"YYYY-MM-DD"` |

<br>

## `economics.csv`

| column                 | data type | description                                                              | cleaning requirements |
| ---------------------- | --------- | ------------------------------------------------------------------------ | --------------------- |
| `client_id`            | `integer` | Client ID                                                                | N/A                   |
| `cons_price_idx`       | `float`   | Consumer price index (monthly indicator)                                 | N/A                   |
| `euribor_three_months` | `float`   | Euro Interbank Offered Rate (euribor) three-month rate (daily indicator) | N/A                   |


In [ ]:
import pandas as pd
import numpy as np


In [334]:
df = pd.read_csv("bank_marketing.csv")

for col in ["credit_default", "mortgage", "previous_outcome", "campaign_outcome"]:
    print(col)
    print("--------------")
    print(df[col].value_counts())
    

credit_default
--------------
no         32588
unknown     8597
yes            3
Name: credit_default, dtype: int64
mortgage
--------------
yes        21576
no         18622
unknown      990
Name: mortgage, dtype: int64
previous_outcome
--------------
nonexistent    35563
failure         4252
success         1373
Name: previous_outcome, dtype: int64
campaign_outcome
--------------
no     36548
yes     4640
Name: campaign_outcome, dtype: int64


In [335]:
df=pd.read_csv("bank_marketing.csv")
df


client_id  age  ... euribor_three_months campaign_outcome
0              0   56  ...                4.857               no
1              1   57  ...                4.857               no
2              2   37  ...                4.857               no
3              3   40  ...                4.857               no
4              4   56  ...                4.857               no
...          ...  ...  ...                  ...              ...
41183      41183   73  ...                1.028              yes
41184      41184   46  ...                1.028               no
41185      41185   56  ...                1.028               no
41186      41186   44  ...                1.028              yes
41187      41187   74  ...                1.028               no

[41188 rows x 16 columns]

In [336]:
client = df[["client_id", "age", "job", "marital", 
                    "education", "credit_default", "mortgage"]]
campaign = df[["client_id", "number_contacts", "month", "day", 
               "contact_duration", "previous_campaign_contacts", "previous_outcome", "campaign_outcome"]]
economics = df[["client_id", "cons_price_idx", "euribor_three_months"]]


In [337]:
df_campaign['month'].unique()

array(['May', 'Jun', 'Jul', 'Aug', 'Oct', 'Nov', 'Dec', 'Mar', 'Apr',
       'Sep'], dtype=object)

In [338]:
df_campaign["last_contact_date"] = pd.to_datetime(df_campaign["month"] + " " + df_campaign["day"].astype(str) + " 2023", format="%b %d %Y")
df_campaign

client_id  number_contacts  ...  day  last_contact_date
0              0                1  ...   13         2023-05-13
1              1                1  ...   19         2023-05-19
2              2                1  ...   23         2023-05-23
3              3                1  ...   27         2023-05-27
4              4                1  ...    3         2023-05-03
...          ...              ...  ...  ...                ...
41183      41183                1  ...   30         2023-11-30
41184      41184                1  ...    6         2023-11-06
41185      41185                2  ...   24         2023-11-24
41186      41186                1  ...   17         2023-11-17
41187      41187                3  ...   23         2023-11-23

[41188 rows x 9 columns]

In [339]:
df_campaign["month"] = df_campaign["month"].str.title()
df_campaign

client_id  number_contacts  ...  day  last_contact_date
0              0                1  ...   13         2023-05-13
1              1                1  ...   19         2023-05-19
2              2                1  ...   23         2023-05-23
3              3                1  ...   27         2023-05-27
4              4                1  ...    3         2023-05-03
...          ...              ...  ...  ...                ...
41183      41183                1  ...   30         2023-11-30
41184      41184                1  ...    6         2023-11-06
41185      41185                2  ...   24         2023-11-24
41186      41186                1  ...   17         2023-11-17
41187      41187                3  ...   23         2023-11-23

[41188 rows x 9 columns]

In [340]:
df_campaign["last_contact_date"] = pd.to_datetime(
    df_campaign["month"] + " " + df_campaign["day"].astype(str) + " 2023",
    format="%b %d %Y"
).dt.date
df_campaign

client_id  number_contacts  ...  day  last_contact_date
0              0                1  ...   13         2023-05-13
1              1                1  ...   19         2023-05-19
2              2                1  ...   23         2023-05-23
3              3                1  ...   27         2023-05-27
4              4                1  ...    3         2023-05-03
...          ...              ...  ...  ...                ...
41183      41183                1  ...   30         2023-11-30
41184      41184                1  ...    6         2023-11-06
41185      41185                2  ...   24         2023-11-24
41186      41186                1  ...   17         2023-11-17
41187      41187                3  ...   23         2023-11-23

[41188 rows x 9 columns]

In [341]:
client["education"] = client["education"].str.replace(".", "_")
client["education"] = client["education"].replace("unknown", np.NaN)


In [342]:
client["job"] = client["job"].str.replace(".", "_")

In [343]:
for col in ["credit_default", "mortgage"]:
  client[col] = client[col].map({"yes": 1,
                                 "no": 0,
                                 "unknown": 0})
  client[col] = client[col].astype(bool)


In [344]:
# Convert "campaign_outcome" to binary values using .map() method
campaign["campaign_outcome"] = campaign["campaign_outcome"].map({"yes": 1, 
                                                                 "no": 0}).astype(bool)

In [345]:
campaign["previous_outcome"] = campaign["previous_outcome"].map({"success": 1, 
                                                                 "failure": 0,
                                                                 "nonexistent": 0}).fillna(0).astype(bool)

In [346]:
campaign["year"] = "2022"

In [347]:
campaign["day"] = campaign["day"].astype(str)

In [348]:
campaign["last_contact_date"] = campaign["year"] + "-" + campaign["month"] + "-" + campaign["day"]


In [349]:
campaign["last_contact_date"] = pd.to_datetime(campaign["last_contact_date"], 
                                               format="%Y-%b-%d")

In [350]:
campaign.drop(columns=["month", "day", "year"], inplace=True)

In [351]:
client.to_csv("client.csv", index=False)
campaign.to_csv("campaign.csv", index=False)
economics.to_csv("economics.csv", index=False)
